In [1]:
from torch.optim.lr_scheduler import ReduceLROnPlateau, CyclicLR
from load_utils import prepare_data
from train_utils import *
from seq2seq_model import *
import numpy as np
import torch
from tqdm.notebook import tnrange, tqdm_notebook
from Calculate_BLEU import *
import datetime

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#device = "cpu"

In [3]:
q, a, pairs, vector = prepare_data('train', 'glove.42B.300d/glove.42B.300d.txt', small=True)

Reading train -------
Read 45544 sentence pairs
Counting words
Counted words:
In questions: 16871 words
In answers: 14637 words


In [4]:
# Add EOS at end of each target sentence
pairs = [[line[0], line[1]+' EOS'] for line in pairs ]

In [5]:
matrix_len = q.n_words
weights_matrix = np.zeros((matrix_len, 300))
word_found = 0
for i, word in enumerate(q.word2index):
    try:
        weights_matrix[i] = vector[word]
    except KeyError:
        weights_matrix[i] = np.random.normal(scale=0.6, size=(300, ))

In [6]:
criterion = nn.NLLLoss()
optimizer = 'Adam'
batch_size = 32
lr = 0.001

In [7]:
model = Seq2Seq(batch_size, q.n_words, a.n_words, 300, 100, weights_matrix, 0.2, device, criterion)

C:\Users\maren\Anaconda3\envs\deeplearning\lib\site-packages\torch\nn\modules\rnn.py:62: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "


In [8]:
if optimizer == 'Adam':
    optimizer = torch.optim.Adam(model.parameters(), lr=lr)
else:
    optimizer = torch.optim.SGD(model.parameters(), lr=lr, momentum=0.9)

In [9]:
#scheduler = ReduceLROnPlateau(optimizer, 'min', patience=5, threshold=0.001, min_lr=1e-6)
#scheduler = CyclicLR(optimizer, base_lr=0.001, max_lr=0.1, step_size_up=500)

In [10]:
a.n_words

14637

In [11]:
from jupyterplot import ProgressPlot

pp = ProgressPlot(x_label='Epoch', plot_names=['train_loss', 'train_accuracy'])

for epoch in tnrange(5, desc="Total epochs: "):

    print(f'Epoch {epoch + 1}: {datetime.datetime.now()}')

    # Calculte loss
    loss = epoch_train(model, optimizer, batch_size, pairs, q, a, device)
    
    #current_lr = optimizer.param_groups[0]['lr']
    
    print(f'Loss: {loss}')
    #print(f'LR: {current_lr}')
    
    #scheduler.step(loss)
    #scheduler.step()

    # Calculate accuracy
    accuracy = epoch_accuray(model, batch_size, pairs, q, a, device)

    print(f'Train accuracy: {accuracy}')

    # Calculate BLEU Score
    #BLEU_model = CalculateBleu(model, batch_size, pairs, q, a, device)
    #bleu_score = BLEU_model.score()

    #print(f'BLUE score: {bleu_score}')

    # Try to do interactive plot
    pp.update([[loss], [accuracy]])

pp.finalize()
print(f"Optimization ended successfully")


<IPython.core.display.Javascript object>

Total epochs:   0%|          | 0/5 [00:00<?, ?it/s]

Epoch 1: 2021-09-23 19:29:38.907610
Loss: 3.5407134856321356
[[3, 4, 5, 6, 7, 8, 6, 9, 10, 11, 12, 13, 14, 15, 2], [16, 3, 9, 17, 18, 19, 20, 21, 15, 22, 23, 24, 25, 26, 27, 28, 29, 30, 15, 31, 32, 33, 19, 2], [20, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 28, 46, 47, 48, 13, 49, 15, 2], [50, 51, 38, 52, 53, 54, 55, 56, 57, 42, 58, 59, 60, 38, 61, 62, 63, 64, 6, 65, 66, 28, 67, 68, 15, 2], [69, 70, 15, 2], [48, 71, 20, 43, 15, 72, 35, 73, 48, 74, 53, 75, 22, 76, 10, 20, 43, 16, 77, 78, 35, 79, 15, 2], [3, 80, 77, 78, 19, 2], [72, 81, 15, 54, 3, 16, 66, 82, 3, 43, 25, 22, 68, 15, 2], [83, 20, 84, 38, 85, 86, 15, 2], [39, 87, 88, 68, 89, 90, 15, 2], [91, 2], [20, 23, 92, 69, 70, 93, 15, 20, 94, 95, 96, 20, 97, 60, 98, 99, 39, 100, 15, 2], [20, 101, 15, 2], [102, 20, 24, 103, 60, 15, 20, 104, 105, 106, 107, 108, 35, 109, 110, 15, 18, 20, 111, 103, 112, 113, 114, 15, 2], [20, 115, 35, 116, 15, 22, 117, 35, 118, 48, 67, 15, 3, 119, 120, 121, 38, 92, 122, 38, 123, 124, 125, 126, 127, 1

[[400, 15, 41, 573, 20, 46, 3, 19, 2], [51, 15, 20, 401, 574, 38, 575, 3, 15, 2], [101, 3, 15, 2], [292, 72, 18, 174, 576, 20, 253, 39, 577, 578, 108, 13, 579, 130, 15, 2], [48, 71, 227, 6, 15, 39, 580, 581, 582, 227, 56, 99, 39, 583, 584, 585, 586, 15, 2], [587, 588, 311, 589, 108, 39, 590, 591, 15, 2], [20, 94, 579, 126, 28, 126, 592, 593, 20, 594, 454, 595, 20, 58, 10, 275, 53, 3, 43, 24, 596, 269, 95, 20, 94, 15, 2], [91, 2], [102, 15, 20, 121, 103, 234, 597, 108, 39, 598, 15, 20, 121, 599, 600, 601, 139, 173, 15, 2], [332, 3, 15, 20, 23, 15, 2], [186, 602, 19, 83, 20, 603, 120, 604, 246, 15, 2], [425, 20, 119, 120, 399, 605, 3, 15, 2], [128, 5, 6, 35, 606, 15, 199, 6, 9, 483, 482, 15, 2], [20, 302, 607, 139, 608, 15, 129, 609, 48, 610, 16, 3, 611, 38, 343, 19, 2], [20, 17, 42, 147, 612, 613, 99, 614, 615, 616, 617, 15, 55, 618, 68, 234, 619, 53, 2], [617, 620, 92, 621, 8, 281, 18, 416, 12, 39, 622, 15, 2], [83, 15, 20, 273, 38, 121, 454, 576, 15, 623, 20, 104, 614, 139, 624, 38, 4

[[128, 744, 15, 2], [128, 134, 20, 991, 248, 15, 227, 992, 491, 371, 993, 15, 20, 994, 35, 995, 28, 996, 207, 15, 306, 425, 54, 310, 953, 156, 418, 15, 2], [20, 115, 10, 400, 8, 485, 186, 295, 15, 269, 186, 108, 156, 764, 19, 2], [20, 473, 5, 39, 997, 620, 288, 38, 998, 39, 999, 557, 469, 1000, 227, 23, 10, 92, 860, 1001, 38, 1002, 39, 1003, 28, 39, 1004, 15, 2], [274, 194, 19, 5, 117, 51, 15, 1005, 54, 42, 121, 68, 89, 404, 5, 23, 121, 35, 416, 1006, 126, 39, 1007, 15, 2], [128, 199, 117, 1008, 15, 271, 259, 38, 1009, 239, 144, 1010, 1011, 15, 2], [20, 253, 1012, 96, 20, 94, 15, 5, 117, 35, 862, 1003, 15, 20, 1013, 34, 3, 683, 593, 3, 56, 108, 156, 780, 1014, 15, 76, 311, 108, 156, 1015, 1016, 54, 3, 121, 35, 11, 1017, 15, 2], [6, 227, 35, 677, 1018, 1019, 735, 519, 28, 615, 404, 108, 3, 764, 19, 2], [519, 302, 771, 615, 404, 382, 1020, 108, 139, 764, 15, 1021, 55, 771, 60, 68, 234, 1020, 15, 2], [91, 2], [121, 3, 326, 481, 38, 1022, 19, 2], [1023, 179, 22, 15, 2], [1024, 53, 72, 11, 

...

[[20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0], [20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0, 2.0, 0.0], [20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0, 2.0], [20.0, 15.0, 3.0, 121.0, 35.0, 11.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0], [20.0, 15.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.

[[487, 15, 8, 54, 265, 35, 1216, 485, 39, 2582, 56, 4927, 1384, 20, 4, 3, 121, 35, 2404, 492, 1429, 1710, 15, 20, 1163, 3, 253, 35, 118, 48, 803, 38, 16, 15, 2], [20, 121, 35, 4928, 108, 139, 4929, 15, 54, 3, 504, 38, 343, 5, 38, 1385, 3, 43, 15, 2], [20, 179, 156, 276, 48, 1889, 35, 1280, 15, 20, 17, 277, 61, 511, 112, 15, 2], [83, 22, 24, 289, 12714, 20, 1385, 12, 156, 1429, 3, 289, 4, 39, 2610, 1710, 15, 20, 23, 15, 2], [269, 89, 1459, 56, 108, 39, 354, 19, 2], [18, 22, 289, 173, 261, 7602, 15, 2502, 101, 5, 306, 10, 3, 15, 425, 15, 2], [91, 2], [1292, 103, 35, 2004, 4279, 48, 2791, 14563, 513, 15, 2], [306, 1720, 2071, 108, 14564, 15, 16, 3, 121, 47, 6039, 3, 58, 550, 52, 19, 2], [39, 1715, 4554, 56, 382, 2295, 501, 39, 2004, 556, 12, 26, 15, 20, 393, 54, 156, 14565, 4081, 694, 15, 2], [128, 72, 299, 308, 2], [35, 1232, 1233, 94, 9835, 139, 229, 28, 1335, 69, 327, 14566, 108, 139, 229, 15, 2], [281, 1474, 22, 94, 975, 227, 15, 2], [20, 121, 38, 61, 38, 3765, 15, 35, 13622, 94, 227,

[[69, 70, 15, 314, 12, 156, 380, 15, 2], [292, 58, 3, 771, 52, 47, 916, 19, 2], [1008, 72, 39, 595, 12, 52, 15, 20, 23, 148, 22, 15, 2], [1695, 1896, 15, 14592, 15, 141, 6, 14200, 3108, 99, 39, 4509, 1482, 5148, 15, 20, 121, 410, 39, 2198, 5641, 12, 3, 15, 2], [375, 15, 758, 92, 5382, 126, 5947, 2124, 1202, 3696, 15, 2], [22, 7202, 1563, 138, 126, 39, 947, 48, 7433, 15, 2], [3, 504, 38, 2093, 317, 354, 15, 6, 5, 3357, 1896, 15, 14592, 19, 2], [134, 20, 121, 103, 3, 219, 317, 354, 1358, 28, 20, 121, 4885, 156, 1998, 15, 156, 417, 2290, 56, 35, 1515, 28, 4099, 15, 2], [292, 55, 56, 15, 20, 121, 4068, 39, 1358, 38, 156, 2044, 2253, 15, 55, 56, 835, 787, 18, 22, 6, 835, 12, 69, 219, 15, 2], [454, 382, 595, 15, 58, 3, 771, 52, 39, 2578, 48, 39, 613, 758, 92, 5382, 63, 19, 2], [69, 70, 15, 516, 69, 202, 15, 121, 35, 324, 1202, 15, 2], [91, 2], [28, 5, 6, 19, 2], [306, 467, 42, 827, 499, 38, 5, 15, 42, 11718, 39, 1042, 63, 3, 513, 108, 9748, 28, 39, 839, 3, 1350, 56, 14593, 108, 113, 2379, 15

[[689, 69, 70, 2], [8, 1591, 3, 272, 3, 258, 1907, 22, 15, 2], [391, 6, 5, 19, 2], [487, 3, 169, 70, 15, 2], [20, 288, 39, 1468, 15, 2], [139, 2107, 407, 139, 2584, 126, 39, 885, 15, 199, 117, 8280, 15, 2], [5323, 3127, 3200, 15, 2], [20, 23, 8, 267, 2872, 15, 2], [91, 2], [400, 15, 365, 6, 22, 19, 2], [69, 70, 15, 365, 16, 3, 504, 52, 38, 446, 19, 2], [375, 15, 269, 234, 19, 2], [269, 89, 19, 2], [246, 959, 19, 2], [375, 15, 269, 234, 16, 3, 504, 52, 38, 446, 19, 35, 9326, 19, 2], [6, 5, 69, 19, 2], [292, 15, 689, 1715, 1204, 48, 6376, 2866, 10996, 28, 35, 1255, 9326, 48, 4423, 15, 2], [20, 17, 18, 15, 2], [91, 2], [22, 117, 186, 166, 662, 117, 661, 15, 2], [20, 43, 120, 1037, 8, 20, 180, 16, 139, 325, 15, 2], [292, 332, 3, 144, 234, 15, 2], [128, 6, 22, 19, 2], [292, 305, 3, 121, 39, 4366, 19, 2], [257, 258, 3, 10094, 304, 38, 13, 674, 63, 39, 4366, 297, 1435, 287, 2728, 22, 15, 2], [91, 2], [292, 15, 141, 759, 267, 15, 2], [20, 3077, 13, 113, 394, 5181, 15, 2], [375, 15, 683, 35, 79

KeyboardInterrupt: 